<a href="https://colab.research.google.com/github/WillemAdriaens3D/FullControl-experiments/blob/main/DoubleSineXYZ.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# FullControl design template

*<<< check out demo models [here](https://github.com/FullControlXYZ/fullcontrol/tree/master/models/README.md) >>>*
  
press ctrl+F9 to run all cells in this notebook, or press shift+enter to run each cell sequentially

if you change one of the code cells, make sure you run it and all subsequent cells again (in order)

*this document is a jupyter notebook - if they're new to you, check out how they work: [link](https://www.google.com/search?q=ipynb+tutorial), [link](https://jupyter.org/try-jupyter/retro/notebooks/?path=notebooks/Intro.ipynb), [link](https://colab.research.google.com/)*
### be patient :)

the next code cell may take a while because running it causes several things to happen:
- connect to a google colab server -> download the fullcontrol code -> install the fullcontrol code

check out [other tutorials](https://github.com/FullControlXYZ/fullcontrol/blob/master/tutorials/README.md) to understand the python code for the FullControl design

In [2]:
if 'google.colab' in str(get_ipython()):
  !pip install git+https://github.com/FullControlXYZ/fullcontrol --quiet
import fullcontrol as fc
from google.colab import files

  Installing build dependencies ... done
  Getting requirements to build wheel ... done
  Preparing metadata (pyproject.toml) ... done


In [50]:
# printer/gcode parameters

design_name = 'my_design'
nozzle_temp = 250
bed_temp = 75
print_speed = 1000
fan_percent = 100
printer_name='generic' # generic / ultimaker2plus / prusa_i3 / ender_3 / cr_10 / bambulab_x1 / toolchanger_T0

In [51]:
# design parameters

EW = 1.7 # extrusion width
EH = 0.2 # extrusion height (and layer height)
initial_z = EH*1.0 # initial nozzle position is set to 0.6x the extrusion height to get a bit of 'squish' for good bed adhesion


In [52]:
!pip install geomdl # Install the geomdl package

import fullcontrol as fc
import numpy as np
from geomdl import NURBS

# ... (Rest of your code) ...

In [56]:
import fullcontrol as fc
import numpy as np
from geomdl import NURBS

# Define NURBS curve parameters (for base radius)
control_points = [(0, 80, 0), (80, 150, 0), (200, 25, 0)]  # Example control points
degree = 2  # Example degree
knot_vector = [0, 0, 0, 1, 1, 1]  # Example knot vector

# Create NURBS curve
curve = NURBS.Curve()
curve.degree = degree
curve.ctrlpts = control_points
curve.knotvector = knot_vector
curve.delta = 0.01  # Adjust for desired point density

# Generate points along the NURBS curve
points = curve.evalpts

# Sine wave parameters
sine_length = 5  # Length of the sine wave along the NURBS curve
sine_amplitude = .1  # Amplitude of the sine wave

# Cylinder parameters
height = 200  # Height of the cylinder
segments = 360  # Number of segments around the cylinder

# Generate cylinder points with sine wave radius variation
cylinder_points = []
for i in range(len(points)):
    base_radius = points[i][1]  # Get base radius from NURBS curve
    # Calculate sine wave offset for radius
    sine_offset = sine_amplitude * np.sin(2 * np.pi * points[i][0] / sine_length)
    radius = base_radius + sine_offset
    for j in range(segments):
        theta = 2 * np.pi * j / segments
        x = radius * np.cos(theta)
        y = radius * np.sin(theta)
        z = points[i][0]  # Use NURBS curve's x-coordinate for cylinder height
        cylinder_points.append(fc.Point(x=x, y=y, z=z))


# Generate steps (fc.Point objects) from cylinder_points
steps = []
for i in range(len(cylinder_points) - 1):
    # Append both points to the steps list to create a "line" effect.
    # This approach assumes the transform function will interpret consecutive
    # fc.Point objects as line segments for plotting.
    steps.append(cylinder_points[i])
    steps.append(cylinder_points[i + 1])

# Preview using the generated steps
fc.transform(steps, 'plot', fc.PlotControls(style='line', zoom=0.7))

In [61]:


import fullcontrol as fc
import numpy as np
from geomdl import NURBS
import math

# ... (Previous code for NURBS curve remains the same) ...

# Sine wave parameters
sine_length_z = 40  # Length of the sine wave along the NURBS curve (z-axis)
sine_amplitude_z = 3  # Amplitude of the sine wave along the NURBS curve
num_sine_waves_xy = 24  # Number of sine waves in each layer (XY-plane)
sine_amplitude_xy = 2  # Amplitude of the sine waves in each layer

# Cylinder parameters
height = 200  # Height of the cylinder
segments = 360  # Number of segments around the cylinder

# Generate cylinder points with sine wave variations in both directions
steps = []
for i in range(len(points)):
    base_radius = points[i][1]  # Get base radius from NURBS curve
    z = points[i][0]  # Use NURBS curve's x-coordinate for cylinder height

    # Calculate sine wave offset for radius along the NURBS curve (z-axis)
    sine_offset_z = sine_amplitude_z * np.sin(2 * np.pi * z / sine_length_z)
    radius = base_radius + sine_offset_z

    for j in range(segments):
        theta = 2 * math.pi * j / segments

        # Calculate sine wave offset for radius within the layer (XY-plane)
        sine_offset_xy = sine_amplitude_xy * np.sin(num_sine_waves_xy * theta)
        radius += sine_offset_xy  # Add to the existing radius

        x = radius * np.cos(theta)
        y = radius * np.sin(theta)

        steps.append(fc.Point(x=x, y=y, z=z))

# Preview or use the cylinder_points in your FullControl design
fc.transform(steps, 'plot', fc.PlotControls(style='line', zoom=0.7))

In [62]:
# generate and save gcode

gcode_controls = fc.GcodeControls(
    printer_name='generic',

    initialization_data={
        'primer': 'front_lines_then_y',
        'print_speed': print_speed,
        'nozzle_temp': 240,
        'bed_temp': bed_temp,
        'fan_percent': fan_percent,
        'extrusion_width': EW,
        'extrusion_height': EH})

gcode = fc.transform(steps, 'gcode', gcode_controls)
open(f'{design_name}.gcode', 'w').write(gcode)


1283968

In [64]:
gcode = fc.transform(steps, 'gcode', gcode_controls)

gcode = gcode.replace("M104 S", "M104 S")
gcode = gcode.replace("M109 S", "M109 S")

# Example to replace specific temperature values
# gcode = gcode.replace("M104 S245", "M104 S245")
# gcode = gcode.replace("M109 S245", "M109 S245")

open(f'{design_name}.gcode', 'w').write(gcode)
files.download(f'{design_name}.gcode')

<IPython.core.display.Javascript object>

<IPython.core.display.Javascript object>

In [30]:
from IPython.display import HTML # Import the HTML class from IPython.display

# Display gcode in an editable text area
display(HTML(f"""
<textarea id="gcode-editor" rows="20" cols="80">{gcode}</textarea>
<button onclick="saveGcode()">Save Gcode</button>
<script>
function saveGcode() {{
  var gcode = document.getElementById('gcode-editor').value;
  // Send gcode to Python for saving (using google.colab.files)
  google.colab.kernel.invokeFunction('save_gcode', [gcode], {{}});
}}
</script>
"""))

# ... (Rest of your code)

In [31]:
from IPython.display import HTML
from google.colab import files

# ... (Your existing code for generating gcode) ...

# Function to save the updated GCODE
def save_gcode(gcode):
  with open(f'{design_name}.gcode', 'w') as f:
    f.write(gcode)
  print(f"GCODE saved to {design_name}.gcode") # Optional: Print confirmation

# Display GCODE in an editable text area with a save button
display(HTML(f"""
<textarea id="gcode-editor" rows="20" cols="80">{gcode}</textarea>
<button onclick="saveGcodeToPython()">Save Gcode</button>
<script>
function saveGcodeToPython() {{
  var updatedGcode = document.getElementById('gcode-editor').value;
  google.colab.kernel.invokeFunction('save_gcode', [updatedGcode], {{}});
}}
</script>
"""))

# (Optional) Trigger a download after saving
# files.download(f'{design_name}.gcode')